<a href="https://colab.research.google.com/github/BoWarburton/DS-Unit-2-Linear-Models/blob/master/Bo_Warburton_LS_DS_213_assignment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science

*Unit 2, Sprint 1, Module 3*

---

# Ridge Regression

## Assignment

We're going back to our other **New York City** real estate dataset. Instead of predicting apartment rents, you'll predict property sales prices.

But not just for condos in Tribeca...

- [X] Use a subset of the data where `BUILDING_CLASS_CATEGORY` == `'01 ONE FAMILY DWELLINGS'` and the sale price was more than 100 thousand and less than 2 million.
- [X] Do train/test split. Use data from January — March 2019 to train. Use data from April 2019 to test.
- [X] Do one-hot encoding of categorical features.
- [X] Do feature selection with `SelectKBest`.
- [X] Do [feature scaling](https://scikit-learn.org/stable/modules/preprocessing.html). Use the scaler's `fit_transform` method with the train set. Use the scaler's `transform` method with the test set.
- [X] Fit a ridge regression model with multiple features.
- [X] Get mean absolute error for the test set.
- [X] As always, commit your notebook to your fork of the GitHub repo.

The [NYC Department of Finance](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page) has a glossary of property sales terms and NYC Building Class Code Descriptions. The data comes from the [NYC OpenData](https://data.cityofnewyork.us/browse?q=NYC%20calendar%20sales) portal.

In [0]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*
    !pip install pandas_profiling==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'
    
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [0]:
import pandas as pd
import pandas_profiling

df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')
df.columns = [col.replace(' ', '_') for col in df]
df['SALE_PRICE'] = (
    df['SALE_PRICE']
    .str.replace('$','')
    .str.replace('-','')
    .str.replace(',','')
    .astype(int)
)

In [0]:
df['BOROUGH'] = df['BOROUGH'].astype(str)

In [0]:
# Get a list of the top 10 neighborhoods
top10 = df['NEIGHBORHOOD'].value_counts()[:10].index

# At locations where the neighborhood is NOT in the top 10, 
# replace the neighborhood with 'OTHER'
df.loc[~df['NEIGHBORHOOD'].isin(top10), 'NEIGHBORHOOD'] = 'OTHER'

In [0]:
# Predict 1 family where sale price > $100k and < $2m
mask = ((df['BUILDING_CLASS_CATEGORY'] == '01 ONE FAMILY DWELLINGS') &
        (df['SALE_PRICE'] > 100000) & 
        (df['SALE_PRICE'] < 2000000))

df = df[mask]

## Do train/test split

Use data from January — March 2019 to train. Use data from April 2019 to test.

In [7]:
df['SALE_DATE'] = pd.to_datetime(df['SALE_DATE'], infer_datetime_format=True)
df['SALE_DATE'].head()

44    2019-01-01
61    2019-01-01
78    2019-01-02
108   2019-01-02
111   2019-01-02
Name: SALE_DATE, dtype: datetime64[ns]

In [8]:
cutoff = pd.to_datetime('2019-04-01')
train = df[df.SALE_DATE < cutoff]
test  = df[df.SALE_DATE >= cutoff]
train.shape, test.shape

((2507, 21), (644, 21))

In [9]:
import pandas_profiling
train.profile_report()

In [15]:
# One-hot encoding
# Check cardinality of non-numeric features
train.describe(exclude='number').T.sort_values(by='unique')

count unique  ...      first       last
BUILDING_CLASS_CATEGORY         2507      1  ...        NaT        NaT
APARTMENT_NUMBER                   1      1  ...        NaT        NaT
TAX_CLASS_AT_PRESENT            2507      2  ...        NaT        NaT
BOROUGH                         2507      5  ...        NaT        NaT
NEIGHBORHOOD                    2507      6  ...        NaT        NaT
BUILDING_CLASS_AT_TIME_OF_SALE  2507     11  ...        NaT        NaT
BUILDING_CLASS_AT_PRESENT       2507     13  ...        NaT        NaT
SALE_DATE                       2507     68  ... 2019-01-01 2019-03-30
LAND_SQUARE_FEET                2507    887  ...        NaT        NaT
ADDRESS                         2507   2497  ...        NaT        NaT

[10 rows x 6 columns]

In [0]:
target = 'SALE_PRICE'
numerics = train.select_dtypes(include='number').columns.drop(target).tolist()
categoricals = train.select_dtypes(exclude='number').columns.tolist()
low_cardinality_categoricals = [col for col in categoricals
                               if train[col].nunique() <= 50]

features = numerics + low_cardinality_categoricals


X_train = train[features]
y_train = train[target]

X_test = test[features]
y_test = test[target]

In [17]:
import category_encoders as ce

encoder = ce.OneHotEncoder(use_cat_names=True)
X_train_encoded = encoder.fit_transform(X_train)
X_test_encoded = encoder.transform(X_test)

X_train_encoded.head()

BLOCK  ...  BUILDING_CLASS_AT_TIME_OF_SALE_S0
44    5495  ...                                  0
61    7918  ...                                  0
78    4210  ...                                  0
108   5212  ...                                  0
111   7930  ...                                  0

[5 rows x 50 columns]

In [0]:
# Drop EASE-MENT, it's null 100% of the time
X_train_encoded = X_train_encoded.drop(columns='EASE-MENT')
X_test_encoded = X_test_encoded.drop(columns='EASE-MENT')

In [0]:
# Filter these warnings:
# sklearn/feature_selection/univariate_selection.py:299: RuntimeWarning: invalid value encountered
# scipy/stats/_distn_infrastructure.py:901: RuntimeWarning: invalid value encountered
warnings.filterwarnings(action='ignore', category=RuntimeWarning, module='sklearn')
warnings.filterwarnings(action='ignore', category=RuntimeWarning, module='scipy')

In [20]:
from sklearn.feature_selection import f_regression, SelectKBest
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train_encoded)
X_test_scaled = scaler.transform(X_test_encoded)

for k in range(1, len(X_train_encoded.columns)+1):
    print(f'{k} features')
    
    selector = SelectKBest(score_func=f_regression, k=k)
    X_train_selected = selector.fit_transform(X_train_scaled, y_train)
    X_test_selected = selector.transform(X_test_scaled)
    
    model = LinearRegression()
    model.fit(X_train_selected, y_train)
    
    y_pred = model.predict(X_test_selected)
    mae = mean_absolute_error(y_test, y_pred)
    print(f'Test MAE: ${mae:,.0f} \n')

1 features
Test MAE: $183,641 

2 features
Test MAE: $182,569 

3 features
Test MAE: $182,569 

4 features
Test MAE: $173,706 

5 features
Test MAE: $175,873 

6 features
Test MAE: $172,843 

7 features
Test MAE: $173,412 

8 features
Test MAE: $173,241 

9 features
Test MAE: $168,685 

10 features
Test MAE: $169,452 

11 features
Test MAE: $169,006 

12 features
Test MAE: $161,221 

13 features
Test MAE: $162,578 

14 features
Test MAE: $161,733 

15 features
Test MAE: $161,735 

16 features
Test MAE: $161,548 

17 features
Test MAE: $161,548 

18 features
Test MAE: $161,308 

19 features
Test MAE: $161,308 

20 features
Test MAE: $159,292 

21 features
Test MAE: $159,371 

22 features
Test MAE: $159,371 

23 features
Test MAE: $159,371 

24 features
Test MAE: $159,048 

25 features
Test MAE: $159,000 

26 features
Test MAE: $158,980 

27 features
Test MAE: $158,970 

28 features
Test MAE: $159,045 

29 features
Test MAE: $159,846 

30 features
Test MAE: $22,819,538,465,805,676 

31 f

In [21]:
# What's going on with k=26?
k = 26
print(f'{k} features')

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train_encoded)
X_test_scaled = scaler.transform(X_test_encoded)

selector = SelectKBest(score_func=f_regression, k=k)
X_train_selected = selector.fit_transform(X_train_scaled, y_train)
X_test_selected = selector.transform(X_test_scaled)

model = LinearRegression()
model.fit(X_train_selected, y_train)

y_pred = model.predict(X_test_selected)
mae = mean_absolute_error(y_test, y_pred)
print(f'Test MAE: ${mae:,.0f} \n')

# Which features were selected?
all_names = X_train_encoded.columns
selected_mask = selector.get_support()
selected_names = all_names[selected_mask]

pd.options.display.float_format = '{:,.0f}'.format
pd.Series(model.coef_, selected_names)

26 features
Test MAE: $158,980 



BLOCK                                -91,329
ZIP_CODE                            -142,910
COMMERCIAL_UNITS                       2,440
TOTAL_UNITS                           -4,116
GROSS_SQUARE_FEET                    122,924
BOROUGH_3                            123,541
BOROUGH_4                            169,114
BOROUGH_2                            -63,351
BOROUGH_5                            -93,541
NEIGHBORHOOD_OTHER                    18,968
NEIGHBORHOOD_FLUSHING-NORTH           38,526
NEIGHBORHOOD_FOREST HILLS             33,680
NEIGHBORHOOD_BOROUGH PARK             20,776
TAX_CLASS_AT_PRESENT_1D                9,266
BUILDING_CLASS_AT_PRESENT_A5          -5,309
BUILDING_CLASS_AT_PRESENT_A3           9,106
BUILDING_CLASS_AT_PRESENT_S1            -669
BUILDING_CLASS_AT_PRESENT_A6          -4,356
BUILDING_CLASS_AT_PRESENT_A8           9,266
BUILDING_CLASS_AT_PRESENT_S0          10,010
BUILDING_CLASS_AT_TIME_OF_SALE_A5    -21,463
BUILDING_CLASS_AT_TIME_OF_SALE_A3      9,106
BUILDING_C

In [22]:
# Ridge regression and mae
from sklearn.feature_selection import f_regression, SelectKBest
from sklearn.linear_model import RidgeCV
from sklearn.metrics import mean_absolute_error
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train_encoded)
X_test_scaled = scaler.transform(X_test_encoded)

for k in range(1, len(X_train_encoded.columns)+1):
    print(f'{k} features')
    
    selector = SelectKBest(score_func=f_regression, k=k)
    X_train_selected = selector.fit_transform(X_train_scaled, y_train)
    X_test_selected = selector.transform(X_test_scaled)
    
    model = RidgeCV()
    model.fit(X_train_selected, y_train)
    
    y_pred = model.predict(X_test_selected)
    mae = mean_absolute_error(y_test, y_pred)
    print(f'Test MAE: ${mae:,.0f} \n')

1 features
Test MAE: $183,670 

2 features
Test MAE: $182,607 

3 features
Test MAE: $182,605 

4 features
Test MAE: $173,757 

5 features
Test MAE: $174,590 

6 features
Test MAE: $172,869 

7 features
Test MAE: $173,390 

8 features
Test MAE: $173,213 

9 features
Test MAE: $168,685 

10 features
Test MAE: $169,454 

11 features
Test MAE: $169,058 

12 features
Test MAE: $161,200 

13 features
Test MAE: $162,515 

14 features
Test MAE: $161,661 

15 features
Test MAE: $161,663 

16 features
Test MAE: $161,474 

17 features
Test MAE: $161,474 

18 features
Test MAE: $161,233 

19 features
Test MAE: $161,233 

20 features
Test MAE: $159,244 

21 features
Test MAE: $159,003 

22 features
Test MAE: $159,029 

23 features
Test MAE: $159,030 

24 features
Test MAE: $159,002 

25 features
Test MAE: $158,955 

26 features
Test MAE: $158,936 

27 features
Test MAE: $158,926 

28 features
Test MAE: $159,000 

29 features
Test MAE: $159,802 

30 features
Test MAE: $159,851 

31 features
Test MA

In [23]:
# Which features were used?
k = 27
selector = SelectKBest(score_func=f_regression, k=k)
X_train_selected = selector.fit_transform(X_train_scaled, y_train)

all_names = X_train_encoded.columns
selected_mask = selector.get_support()
selected_names = all_names[selected_mask]
unselected_names = all_names[~selected_mask]

print('Features selected:')
for name in selected_names:
    print(name)

print('\nFeatures not selected:')
for name in unselected_names:
    print(name)

Features selected:
BLOCK
ZIP_CODE
COMMERCIAL_UNITS
TOTAL_UNITS
GROSS_SQUARE_FEET
BOROUGH_3
BOROUGH_4
BOROUGH_2
BOROUGH_5
NEIGHBORHOOD_OTHER
NEIGHBORHOOD_FLUSHING-NORTH
NEIGHBORHOOD_FOREST HILLS
NEIGHBORHOOD_BOROUGH PARK
TAX_CLASS_AT_PRESENT_1
TAX_CLASS_AT_PRESENT_1D
BUILDING_CLASS_AT_PRESENT_A5
BUILDING_CLASS_AT_PRESENT_A3
BUILDING_CLASS_AT_PRESENT_S1
BUILDING_CLASS_AT_PRESENT_A6
BUILDING_CLASS_AT_PRESENT_A8
BUILDING_CLASS_AT_PRESENT_S0
BUILDING_CLASS_AT_TIME_OF_SALE_A5
BUILDING_CLASS_AT_TIME_OF_SALE_A3
BUILDING_CLASS_AT_TIME_OF_SALE_S1
BUILDING_CLASS_AT_TIME_OF_SALE_A6
BUILDING_CLASS_AT_TIME_OF_SALE_A8
BUILDING_CLASS_AT_TIME_OF_SALE_S0

Features not selected:
LOT
RESIDENTIAL_UNITS
YEAR_BUILT
TAX_CLASS_AT_TIME_OF_SALE
BOROUGH_1
NEIGHBORHOOD_BEDFORD STUYVESANT
NEIGHBORHOOD_ASTORIA
BUILDING_CLASS_CATEGORY_01 ONE FAMILY DWELLINGS
BUILDING_CLASS_AT_PRESENT_A9
BUILDING_CLASS_AT_PRESENT_A1
BUILDING_CLASS_AT_PRESENT_A0
BUILDING_CLASS_AT_PRESENT_A2
BUILDING_CLASS_AT_PRESENT_A4
BUILDING_CLASS_A